In [1]:
import os
import sys
import gc
import pickle
import warnings
import pandas as pd
import numpy as np
import seaborn as sns
from typing import *
from tqdm.notebook import tqdm
from pathlib import Path
from matplotlib import pyplot as plt

pd.set_option('max_columns', 50)
pd.set_option('max_rows', 200)
warnings.simplefilter('ignore')
sns.set()

In [2]:
base_dir = Path().resolve()
sys.path.append(str(base_dir / '../'))

from utils.preprocess import *
from utils.model import *
from utils.train import *
from utils.eval import *
from utils.detectron2helper import *

fail to import apex_C: apex was not installed or installed without --cpp_ext.
fail to import amp_C: apex was not installed or installed without --cpp_ext.
** fvcore version of PathManager will be deprecated soon. **
** Please migrate to the version in iopath repo. **
https://github.com/facebookresearch/iopath 

** fvcore version of PathManager will be deprecated soon. **
** Please migrate to the version in iopath repo. **
https://github.com/facebookresearch/iopath 



HACKING: overriding COCOeval.summarize = vin_summarize...


In [3]:
from dataclasses import dataclass, field, asdict
import yaml


@dataclass
class Config:
    # General
    outdir: str = "yolov5_results/results02"
    datadir: str = "../../data/yolov5_data"
    device: str = "cuda:1"
    device_id: int = 1
    num_workers: int = 8
        
    # Training config
    batch_size: int = 4

    # Data config
    imgconf_file: str = '../../data/VinBigData/train.csv'
    meta_file: str = '../../data/VinBigData/train_meta.csv'
    test_meta_file: str = '../../data/VinBigData/test_meta.csv'
    imgdir_name: str = "../../data/VinBigData/png512"
    img_size: int = 512
    seed: int = 111
    n_splits: int = 5
    conf_thr: float = 0.0
       
    def update(self, param_dict: Dict) -> "Config":
        # Overwrite by `param_dict`
        for key, value in param_dict.items():
            if not hasattr(self, key):
                raise ValueError(f"[ERROR] Unexpected key for flag = {key}")
            setattr(self, key, value)
        return self
    
    def to_yaml(self, filepath: str, width: int = 120):
        with open(filepath, 'w') as f:
            yaml.dump(asdict(self), f, width=width)

In [4]:
config = Config()

In [5]:
def seed_everything(seed: int, device: str):
    random.seed(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True
    with torch.cuda.device(device):
        torch.cuda.empty_cache()

In [6]:
classes_nms = [
    "Aortic enlargement",
    "Atelectasis",
    "Calcification",
    "Cardiomegaly",
    "Consolidation",
    "ILD",
    "Infiltration",
    "Lung Opacity",
    "Nodule/Mass",
    "Other lesion",
    "Pleural effusion",
    "Pleural thickening",
    "Pneumothorax",
    "Pulmonary fibrosis",
#     "No Finding"
]
classes_dict = {index: class_name  for index, class_name in enumerate(classes_nms)}

In [7]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.patches as patches
import seaborn as sns
from pathlib import Path
import json
import re
import logging
import gc
import random
import warnings
from tqdm.notebook import tqdm
from PIL import Image
import os
from glob import glob
from joblib import Parallel, delayed
import shutil as sh
from itertools import product
from collections import OrderedDict
from iterstrat.ml_stratifiers import MultilabelStratifiedKFold
from ensemble_boxes import nms, weighted_boxes_fusion
import torchvision.transforms as transforms
import albumentations as al
from albumentations import ImageOnlyTransform
from albumentations.pytorch import ToTensorV2, ToTensor
from albumentations.core.transforms_interface import DualTransform, ImageOnlyTransform

import cv2
# import pydicom
from IPython.display import display, Image
from sklearn.model_selection import train_test_split, KFold, GroupKFold, StratifiedKFold
import torch
from torch.nn import functional as f
import torch.nn as nn
from torch.optim import Adam
from torch.optim.lr_scheduler import StepLR, ReduceLROnPlateau, CosineAnnealingLR
from torch.utils.data import Dataset, DataLoader, sampler
import timm
# from efficientnet_pytorch import EfficientNet

pd.options.display.max_columns = None
warnings.filterwarnings('ignore')

logging.basicConfig(format='%(asctime)s +++ %(message)s',
                    datefmt='%d-%m-%y %H:%M:%S', level=logging.INFO)
logger = logging.getLogger()

device = torch.device(config.device if torch.cuda.is_available() else 'cpu')
logger.info(device)

30-03-21 12:01:12 +++ cuda:1


In [6]:
for fold in tqdm(range(config.n_splits)):
    outdir = base_dir / config.outdir / f'fold-{fold + 1}'
    exp_dir = outdir / 'runs' / 'train'
    exp_last = sorted(os.listdir(str(exp_dir)))[-1]
    weight_path = str(exp_dir / exp_last / 'weights' / 'best.pt')

    valid_data_path = str(base_dir / 'chest_yolo' / f'{config.img_size}_mkf_{fold + 1}' / 'images' / 'val')
    project_dir = str(outdir / 'runs' / 'detect')
    
    !python ./yolov5/detect.py --weights $weight_path --img-size $config.img_size --conf-thres 0.0 --source $valid_data_path --iou-thres 0.0 --save-txt --save-conf --project $project_dir --device $config.device_id

  0%|          | 0/5 [00:00<?, ?it/s]

Namespace(agnostic_nms=False, augment=False, classes=None, conf_thres=0.0, device='1', exist_ok=False, img_size=512, iou_thres=0.0, name='exp', project='/home/yamaguchi-milkcocholate/VinBigData/src/VinBigData-ObjectDetection/yolov5_results/results02/fold-1/runs/detect', save_conf=True, save_txt=True, source='/home/yamaguchi-milkcocholate/VinBigData/src/VinBigData-ObjectDetection/chest_yolo/512_mkf_1/images/val', update=False, view_img=False, weights=['/home/yamaguchi-milkcocholate/VinBigData/src/VinBigData-ObjectDetection/yolov5_results/results02/fold-1/runs/train/exp2/weights/best.pt'])
YOLOv5  torch 1.7.1+cu101 CUDA:1 (Tesla V100-PCIE-32GB, 32510.5MB)

Fusing layers... 
Model Summary: 476 layers, 87286171 parameters, 0 gradients, 217.4 GFLOPS
image 1/874 /home/yamaguchi-milkcocholate/VinBigData/src/VinBigData-ObjectDetection/chest_yolo/512_mkf_1/images/val/001d127bad87592efe45a5c7678f8b8d.png: 512x512 20 Aortic enlargements, 12 Atelectasiss, 23 Calcifications, 17 Cardiomegalys, 12 Co

In [8]:
def to_objects(detect_result, conf_thr):
    objs = np.array(list(map(float, re.split(r'[\n ]', detect_result)[:-1]))).reshape(-1, 6)

    labels = objs[:, 0]
    x_centers = objs[:, 1].copy()
    y_centers = objs[:, 2].copy()
    widths = objs[:, 3].copy()
    heights = objs[:, 4].copy()
    scores = objs[:, 5]

    x_mins = x_centers - 0.5 * widths
    x_maxs = x_centers + 0.5 * widths
    y_mins = y_centers - 0.5 * heights
    y_maxs = y_centers + 0.5 * heights
    boxes = np.vstack([x_mins, y_mins, x_maxs, y_maxs]).T

    mask = (scores > conf_thr)
    boxes = boxes[mask, :]
    labels = labels[mask]
    scores = scores[mask]
    
    return boxes, labels, scores

In [9]:
iou_thresh = 0.4
iou_thresh2 = 0.1
iou_thresh11 = 0.0001
score_last = 0.0
score_last2 = 0.95
score_9 = 0.1
score_11 = 0.015

In [10]:
# make validation.csv
for fold in range(config.n_splits):
    outdir = base_dir / config.outdir / f'fold-{fold + 1}' 
    pred_dir = outdir / 'runs' / 'detect' / 'exp' / 'labels'
    files = sorted(os.listdir(pred_dir))
    files = [f for f in files if '.txt' in f]

    records = {'image_id': list(), 'PredictionString': list()}

    for file in tqdm(files):
        filepath = str(pred_dir / file)
        with open(filepath, 'r+') as f:
            detect_result = f.read()
        boxes, labels, scores = to_objects(detect_result, score_last)

        boxes_, labels_, scores_ = list(), list(), list()
        for cls_id in range(len(classes_nms)):
            mask = (labels == cls_id)
            if mask.sum() == 0:
                continue
            elif mask.sum() == 1:
                p_boxes, p_scores, p_labels = boxes[mask, :], scores[mask], labels[mask]
            else:
                if cls_id == 2:
                    p_boxes, p_scores, p_labels = nms([boxes[mask, :]], [scores[mask]], [labels[mask]], weights=None, iou_thr=iou_thresh2)
                elif cls_id == 11:
                    p_boxes, p_scores, p_labels = nms([boxes[mask, :]], [scores[mask]], [labels[mask]], weights=None, iou_thr=iou_thresh11)
                else:
                    p_boxes, p_scores, p_labels = nms([boxes[mask, :]], [scores[mask]], [labels[mask]], weights=None, iou_thr=iou_thresh)
            
            if cls_id == 9:
                mask = (p_scores > score_9)
            elif cls_id == 11:
                mask = (p_scores > score_11)
            else:
                mask = (p_scores > score_last)

            p_boxes *= config.img_size

            boxes_ += p_boxes[mask].tolist()
            labels_ += p_labels[mask].tolist()
            scores_ += p_scores[mask].tolist()

        pred_str = list()
        for label, score, box in zip(labels_, scores_, boxes_):
            pred_str += [str(int(label))] + [str(np.round(score, 3))] + np.array(box).astype(int).astype(str).tolist()

        records['image_id'] += [file.replace('.txt', '')]
        records['PredictionString'] += [' '.join(pred_str)]

    pred_df = pd.DataFrame(records)
    pred_df.to_csv(str(outdir / 'validation_nms.csv'))

  0%|          | 0/874 [00:00<?, ?it/s]

Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 3 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixe

  0%|          | 0/897 [00:00<?, ?it/s]

Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes

  0%|          | 0/887 [00:00<?, ?it/s]

Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes

  0%|          | 0/871 [00:00<?, ?it/s]

Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check tha

  0%|          | 0/865 [00:00<?, ?it/s]

Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates < 0
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 2 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordinates > 1. Check that your boxes was normalized at [0, 1]
Warning. Fixed 1 boxes coordinates < 0
Warning. Fixed 1 boxes coordina

In [22]:
def load_train_data(filepath: str, meta_filepath: str, img_size: int) -> pd.DataFrame:
    train = pd.read_csv(filepath)
    train.fillna(0, inplace=True)
    train.loc[train["class_id"] == 14, ['x_max', 'y_max']] = 1.0
    
    train_meta = pd.read_csv(meta_filepath)
    
    train = pd.merge(train, train_meta, how='left', on='image_id')
    
    train[f'x_min_{img_size}'] = (img_size / train['dim1'] * train['x_min'])
    train[f'x_max_{img_size}'] = (img_size / train['dim1'] * train['x_max'])
    train[f'y_min_{img_size}'] = (img_size / train['dim0'] * train['y_min'])
    train[f'y_max_{img_size}'] = (img_size / train['dim0'] * train['y_max'])
    
    return train

In [24]:
train = load_train_data(str(base_dir / config.imgconf_file), str(base_dir / config.meta_file), 1024)
cor_cols = ['x_min', 'y_min', 'x_max', 'y_max']
train = train.drop(columns=cor_cols)
train = train.rename(columns={f'{c}_{1024}': c for c in cor_cols})
train.head()

image_id          class_name  class_id rad_id  \
0  50a418190bc3fb1ef1633bf9678929b3          No finding        14    R11   
1  21a10246a5ec7af151081d0cd6d65dc9          No finding        14     R7   
2  9a5094b2563a1ef3ff50dc5c7ff71345        Cardiomegaly         3    R10   
3  051132a778e61a86eb147c7c6f564dfe  Aortic enlargement         0    R10   
4  063319de25ce7edb9b1c6b8881290140          No finding        14    R10   

   dim0  dim1       x_min       x_max       y_min       y_max  
0  2580  2332    0.000000    0.439108    0.000000    0.396899  
1  3159  2954    0.000000    0.346649    0.000000    0.324153  
2  2336  2080  340.184615  813.784615  602.739726  802.630137  
3  2880  2304  561.777778  716.000000  264.177778  362.311111  
4  3072  2540    0.000000    0.403150    0.000000    0.333333

In [25]:
fold = 0
outdir = base_dir / 'yolov5_results/results01' / f'fold-{fold + 1}'
pred_df = pd.read_csv(outdir / 'validation_nms.csv', index_col=0)
pred_df = pred_df[~pred_df['PredictionString'].isnull()]  # incorrectly contains Nan
pred_df.head()

image_id  \
0  001d127bad87592efe45a5c7678f8b8d   
1  008b3176a7248a0a189b5731ac8d2e95   
2  00bcb82818ea83d6a86df241762cd7d0   
3  00f2f97f74e086e1f82acc285ee4a5c5   
4  01570ee44031e4ebab6031501293bf66   

                                    PredictionString  
0  0 0.461 501 224 590 322 0 0.001 328 118 446 29...  
1  0 0.159 491 199 603 295 0 0.002 352 416 778 55...  
2  0 0.642 475 219 572 316 0 0.002 329 504 712 64...  
3  0 0.298 478 222 592 318 0 0.002 353 437 794 54...  
4  0 0.058 460 257 570 378 0 0.001 257 312 400 43...

In [26]:
train_fold = train.query(f"image_id in {pred_df['image_id'].values.tolist()}")
train_fold = train_fold.reset_index()
evaluator = VinBigDataEval(train_fold)

Generating image data...
Generating category data...
Generating annotation data...


In [27]:
evaluator.evaluate(pred_df)

Generating prediction data...
creating index...
index created!
creating index...
index created!
Running per image evaluation...
Evaluate annotation type *bbox*
DONE (t=2.83s).
Accumulating evaluation results...
DONE (t=0.64s).
 Average Precision  (AP) @[ IoU=0.40:0.40 | area=   all | maxDets=100 ] = 0.358
 Average Precision  (AP) @[ IoU=0.50      | area=   all | maxDets=100 ] = -1.000
 Average Precision  (AP) @[ IoU=0.40      | area=   all | maxDets=100 ] = 0.358
 Average Precision  (AP) @[ IoU=0.40:0.40 | area= small | maxDets=100 ] = 0.408
 Average Precision  (AP) @[ IoU=0.40:0.40 | area=medium | maxDets=100 ] = 0.434
 Average Precision  (AP) @[ IoU=0.40:0.40 | area= large | maxDets=100 ] = 0.393
 Average Recall     (AR) @[ IoU=0.40:0.40 | area=   all | maxDets=  1 ] = 0.373
 Average Recall     (AR) @[ IoU=0.40:0.40 | area=   all | maxDets= 10 ] = 0.610
 Average Recall     (AR) @[ IoU=0.40:0.40 | area=   all | maxDets=100 ] = 0.657
 Average Recall     (AR) @[ IoU=0.40:0.40 | area= sm

In [47]:
pred_df.loc[0, 'PredictionString']

'0.0 0.460693 501.99956480000003 224.0004608 590.9996032 322.0004352 2.0 0.141357 344.9998848 121.00044799999999 433.9999232 308.000256 2.0 0.0525818 686.0001791999999 282.99970559999997 700.0002048 293.9997184 8.0 0.195557 686.0001791999999 282.99970559999997 700.0002048 293.9997184 8.0 0.05896 701.0000384 213.00008960000002 714.0000256000001 224.0001024 8.0 0.0536499 348.00045056 231.00009472000002 358.00044544 238.00009728 11.0 0.185303 319.9997952 110.00017919999999 405.99982079999995 156.0002048 13.0 0.414307 388.9995776 123.00001280000001 415.99959040000005 164.9999872 13.0 0.239502 284.999936 288.0001024 372.999936 348.00015360000003 13.0 0.0530396 685.999616 282.99970559999997 701.999616 293.9997184'